In [2]:
import nltk
import pandas as pd
import re
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem.snowball import SnowballStemmer
from nltk.stem.porter import PorterStemmer


In [3]:
file=pd.read_csv("sells.csv")
file

company    type  amount                 date
0        TOO Metal House  ferrum      61  2020-07-01 08:03:21
1        TOO Metal House  ferrum       3  2020-07-01 08:03:21
2        TOO Metal House    alum      47  2020-07-01 08:03:22
3       TOO UshaqQurylys  ferrum      79  2020-07-01 08:03:23
4         TOO VagonStroi  ferrum      27  2020-07-01 08:03:24
...                  ...     ...     ...                  ...
354163    TOO VagonStroi  ferrum      78  2021-04-01 17:46:33
354164    TOO VagonStroi  ferrum      15  2021-04-01 17:46:37
354165   TOO Metal House  ferrum       8  2021-04-01 17:46:37
354166   TOO Metal House  ferrum      42  2021-04-01 17:46:38
354167  TOO UshaqQurylys    a um       7  2021-04-01 17:46:39

[354168 rows x 4 columns]

In [13]:
def f(file):
    text = file['type']
    tokens = word_tokenize(text)
    
    # remove punctuation from each word
    import string
    table = str.maketrans('', '', string.punctuation)
    words = [w.translate(table) for w in tokens]
    # converting list to string
    s = ' '
    cleaned_type = s.join(words)
    return cleaned_type

In [14]:
for index, row in file.iterrows():
    file.at[index,'cleaned_type'] = ''.join(f(row))
file

company    type  amount                 date cleaned_type
0        TOO Metal House  ferrum      61  2020-07-01 08:03:21       ferrum
1        TOO Metal House  ferrum       3  2020-07-01 08:03:21       ferrum
2        TOO Metal House    alum      47  2020-07-01 08:03:22         alum
3       TOO UshaqQurylys  ferrum      79  2020-07-01 08:03:23       ferrum
4         TOO VagonStroi  ferrum      27  2020-07-01 08:03:24       ferrum
...                  ...     ...     ...                  ...          ...
354163    TOO VagonStroi  ferrum      78  2021-04-01 17:46:33       ferrum
354164    TOO VagonStroi  ferrum      15  2021-04-01 17:46:37       ferrum
354165   TOO Metal House  ferrum       8  2021-04-01 17:46:37       ferrum
354166   TOO Metal House  ferrum      42  2021-04-01 17:46:38       ferrum
354167  TOO UshaqQurylys    a um       7  2021-04-01 17:46:39         a um

[354168 rows x 5 columns]

In [5]:
# Kazakh_Stemmer.py
# I could import it, but could use as module
# so I just wrote it here
import re
import nltk
import pandas as pd
from nltk.corpus import stopwords

class Kazakh_Stemmer:
    def __init__(self, text):
        self.data = pd.read_csv('zhalgaular_zhurnaktar.csv')
        self.endings = self.data['aty'].tolist()
        self.endings.sort(key=len, reverse=True)
        self.tokens = self.text_processing(text)
        self.min_word_length = 2
        self.cleared_tokens = []
        self.cleared_tokens.append([self.stem(token) for token in self.tokens])
        self.stemmed_text = ' '.join(self.cleared_tokens[0])
        self.text = self.stemmed_text

    def text_processing(self, text):
        text = text.lower()
        text = re.sub('[^a-zA-Zа-яА-ЯӘІҢҒҮҰҚӨәіңғүұқөһ]', ' ', text)
        tokens = []
        words_to_remove = []
        stop_words_kazakh = set(stopwords.words('kazakh'))
        stop_words_english = set(stopwords.words('english'))
        for i in stop_words_kazakh:
            if i=='емес' or i=='жоқ':
                words_to_remove.append(i)
        for i in words_to_remove:
            stop_words_kazakh.remove(i)
        tokens = nltk.word_tokenize(text)
        tokens = [t for t in tokens if t not in stop_words_kazakh]
        tokens = [t for t in tokens if t not in stop_words_english]
        return tokens

    def matcher(self, token):
        reg = re.compile("[аәоөұүыіеиуёэюя]")
        l = reg.findall(token)
        if len(l) >= 2:
            return False
        else:
            return True

    def stem(self, word):
        if(len(word) <= self.min_word_length or self.matcher(word)):
            return word
        for ending in self.endings:
            if word.endswith(ending):
                trimmed = word[:-len(ending)]
                return self.stem(trimmed)
        n = len(word)
        word_list = list(word)
        if word_list[n-1] == 'б':
            word_list[n-1] = 'п'
        if word_list[n-1] == 'д':
            word_list[n-1] = 'т'
        if word_list[n-1] == 'ғ':
            word_list[n-1] = 'қ'
        if word_list[n-1] == 'г':
            word_list[n-1] = 'к'
        word = ''.join(word_list)
        return word

In [6]:
def lab7(file):
    snowball_russian = SnowballStemmer(language="russian")
    english_stemmer = PorterStemmer()
    stop_words_russian = set(stopwords.words('russian'))
    stop_words_english = set(stopwords.words('english'))
    for index, row in file.iterrows():
        if row['language'] == 'ru': # Russian stemmer
            tokens = word_tokenize(row['cleaned_text'])
            remove_stop_words = [t for t in tokens if t not in (stop_words_russian and stop_words_english)]
            russian_stemming = [snowball_russian.stem(t) for t in remove_stop_words]
            english_stemming = [english_stemmer.stem(t) for t in russian_stemming]
            stemming = russian_stemming
        else: # Kazakh stemmer by using Kazakh_Stemmer class
            kz = Kazakh_Stemmer(row['cleaned_text'])
            tokens = kz.text_processing(row['cleaned_text'])
            kazakh_stemming = [kz.stem(t) for t in tokens]
            stemming = kazakh_stemming
        file.at[index,'cleaned_text1'] = ' '.join(stemming)
    return file

In [7]:
file1 = lab7(file)
file1

Unnamed: 0      id                                               text  \
0               0    3356                                   НАШ ОТВЕТ ЕЛБАСЫ   
1               1   77040  Еще 48 новых случаев COVID-19 выявлено в Казах...   
2               2    3354   Елбасы Юкия Аманоның отбасы мүшелерімен кездесті   
3               3    3353                        Столица, построенная Елбасы   
4               4    3352                               Елбасы салған Елорда   
...           ...     ...                                                ...   
97913       97913  197132  В Армении протестующие против соглашения о пре...   
97914       97914  197134  Президент Армении заявил, что узнал о подписан...   
97915       97915  197123  Министр информации и общественного развития РК...   
97916       97916  197133  В Казахстане отмечают 75-ю годовщину Победы со...   
97917       97917  197135  Пресс-служба Первого Президента РК Нурсултана ...   

       language_id  tonal_id  id.1          name language  \
0                4       2.0     4  Неопределено       ru   
1                4       3.0     4  Неопределено       ru   
2                4       2.0     4  Неопределено       kk   
3                4       2.0     4  Неопределено       ru   
4                4       2.0     4  Неопределено       kk   
...            ...       ...   ...           ...      ...   
97913            4       1.0     4  Неопределено       ru   
97914            4       1.0     4  Неопределено       ru   
97915            4       2.0     4  Неопределено       ru   
97916            4       2.0     4  Неопределено       ru   
97917            4       2.0     4  Неопределено       ru   

                                            cleaned_text  \
0                                       наш ответ елбасы   
1      новых случаев выявлено казахстане общее число ...   
2       елбасы юкия аманоның отбасы мүшелерімен кездесті   
3                             столица построенная елбасы   
4                                   елбасы салған елорда   
...                                                  ...   
97913  армении протестующие против соглашения прекращ...   
97914  президент армении заявил узнал подписании доку...   
97915  министр информации общественного развития рк а...   
97916  казахстане отмечают годовщину победы советског...   
97917  прессслужба первого президента рк нурсултана н...   

                                           cleaned_text1  
0                                        наш ответ елбас  
1      нов случа выявл казахстан общ числ превыс полт...  
2                             ел юкия амано от мү кездес  
3                                  столиц построен елбас  
4                                             ел сал ело  
...                                                  ...  
97913  армен протест прот соглашен прекращен боев дей...  
97914  президент армен заяв узна подписан документ пр...  
97915  министр информац обществен развит рк аид балае...  
97916  казахстан отмеча годовщин побед советск народ ...  
97917  прессслужб перв президент рк нурсулта назарбае...  

[97918 rows x 10 columns]

In [15]:
# split our data to vectorize the text
def splitting(file):
    l =[]
    for i in range(len(file['cleaned_text1'])):
        l.append(file['cleaned_text1'][i].split())
    return l
splitted_lists = splitting(file1)
splitted_lists

[['наш', 'ответ', 'елбас'],
 ['нов',
  'случа',
  'выявл',
  'казахстан',
  'общ',
  'числ',
  'превыс',
  'полтор',
  'тысяч',
  'казахста',
  'обнов',
  'рекордн',
  'дневн',
  'прирост',
  'количеств',
  'заболевш',
  'https'],
 ['ел', 'юкия', 'амано', 'от', 'мү', 'кездес'],
 ['столиц', 'построен', 'елбас'],
 ['ел', 'сал', 'ело'],
 ['ел', 'н', 'до', 'нақ', 'іс', 'көшу', 'қажет'],
 ['нұро', 'о', 'си', 'ел', 'кім', 'не', 'сын'],
 ['назарба', 'остав', 'джакишев', 'тюрьм'],
 ['ел', 'юкия', 'амано', 'от', 'мү', 'кездес'],
 ['назарба',
  'две',
  'коров',
  'неудобн',
  'правд',
  'елбас',
  'казахста',
  'сих',
  'пор',
  'шок',
  'слов'],
 ['назарба',
  'кок',
  'обижа',
  'мо',
  'мам',
  'меньш',
  'тиран',
  'твор',
  'справедлив',
  'помог',
  'многодетн',
  'мам'],
 ['ел', 'ба', 'кө', 'айлық', 'аздық', 'айт', 'а', 'жаят', 'қа', 'сын', 'ал'],
 ['куп', 'две', 'коров', 'реч', 'елбас'],
 ['назарбаев', 'байбек', 'пода', 'суд', 'бас'],
 ['ел', 'ре', 'қазақс', 'елш', 'кездес'],
 ['дом', '

In [19]:
from collections import Counter
import math

# Lab8 TF-IDF 
def compute_tfidf(slist):
    def compute_tf(text):
        tf_text = Counter(text)
        for i in tf_text:
            tf_text[i] = tf_text[i]/float(len(text))
        return tf_text
    def compute_idf(word, slist):
        return math.log10(len(slist)/sum([1.0 for i in slist if word in i]))

    documents_list = []
    for text in slist:
        tf_idf_dictionary = {}
        computed_tf = compute_tf(text)
        for word in computed_tf:
            tf_idf_dictionary[word] = computed_tf[word] * compute_idf(word, slist)
        documents_list.append(tf_idf_dictionary)
    return documents_list

# Sorry, I waited hours for the full results to be displayed, but this was overloading my laptop, so I split the data up.
# I also tried to split into Kazakh and Russian text, but this overloaded my laptop too

In [22]:
print(compute_tfidf(splitted_list[:500])) 

[{'наш': 0.3304666094126941, 'ответ': 0.5076262484267792, 'елбас': 0.28882036387659415}, {'нов': 0.06867594631139785, 'случа': 0.09323686188406953, 'выявл': 0.15876294143153052, 'казахстан': 0.07103578297069095, 'общ': 0.09323686188406953, 'числ': 0.08223176521600221, 'превыс': 0.14105529462776692, 'полтор': 0.13069698527155035, 'тысяч': 0.07979690138316545, 'казахста': 0.04242625876748065, 'обнов': 0.14105529462776692, 'рекордн': 0.15876294143153052, 'дневн': 0.15876294143153052, 'прирост': 0.15876294143153052, 'количеств': 0.08793235421647612, 'заболевш': 0.13069698527155035, 'https': 0.06583449457171815}, {'ел': 0.2086353288322999, 'юкия': 0.39965666811200623, 'амано': 0.39965666811200623, 'от': 0.3333333333333333, 'мү': 0.3333333333333333, 'кездес': 0.3333333333333333}, {'столиц': 0.5176139895525935, 'построен': 0.6989700043360187, 'елбас': 0.28882036387659415}, {'ел': 0.4172706576645998, 'сал': 0.6666666666666666, 'ело': 0.598626672448025}, {'ел': 0.17883028185625707, 'н': 0.28571

In [25]:
print(compute_tfidf(splitted_list[500:1000])) 

[{'mega': 0.11036368489516085, 'silk': 0.10526315789473684, 'way': 0.10526315789473684, 'с': 0.07474823175701, 'орталық': 0.07867631693053126, 'қр': 0.07357578993010724, 'ақпарат': 0.07246056366326839, 'жән': 0.04429671094235528, 'қо': 0.05831081038471156, 'даму': 0.06757877138764214, 'минист': 0.08015151290949145, 'меломан': 0.11036368489516085, 'компания': 0.09757220864851379, 'өз': 0.07038116675360136, 'ынтымақтас': 0.10526315789473684, 'жөн': 0.07246056366326839, 'меморанду': 0.11036368489516085, 'қол': 0.05951412001415914, 'қойыл': 0.08015151290949145}, {'чита': 0.09182776288929968, 'книг': 0.07598407890698487, 'стан': 0.12620736887747566, 'духовн': 0.08172852466619898, 'богат': 0.11036368489516085, 'спонсор': 0.12620736887747566, 'конкурс': 0.15196815781396975, 'явля': 0.050453016570619735, 'министерств': 0.06940835592760067, 'информац': 0.0667161179040543, 'обществен': 0.04846414494486185, 'развит': 0.05004115670156939, 'рк': 0.048848315404940765, 'компан': 0.07357578993010724, 

In [26]:
print(compute_tfidf(splitted_list[1000:1500])) 

[{'қазақс': 0.11944938220444468, 'авто': 0.20761307725661685, 'та': 0.12192512707916786, 'шы': 0.18445692374400288, 'тұң': 0.17091144227818125, 'рет': 0.16130077023138895, 'бір': 0.1342098072997457, 'ә': 0.11714451886771829, 'не': 0.14260553571705864, 'ал': 0.0898070067149049, 'тіл': 0.18445692374400288, 'аударыл': 0.20761307725661685, 'о': 0.13814461671877504}, {'ожида': 0.3105683937315562, 'концепц': 0.4443697499232713, 'принят': 0.31700533040583645, 'конц': 0.3105683937315562, 'год': 0.15289431061849024}, {'қaзaқтap': 1.3494850021680094, 'виккингтep': 1.3494850021680094}, {'педагогическ': 0.07102552642989522, 'круг': 0.055181842447580426, 'шахтерск': 0.07102552642989522, 'кра': 0.05846970393727253, 'практическ': 0.05263157894736842, 'одновремен': 0.07102552642989522, 'стрясл': 0.07102552642989522, 'одинаков': 0.06310368443873783, 'сканда': 0.055181842447580426, 'бухгалтер': 0.06310368443873783, 'областн': 0.04470973695621102, 'специальн': 0.04362045576783668, 'школыинтернат': 0.0710